In [46]:
import numpy as np
import pandas as pd
import folium
import json
import requests
import seaborn as sns
import datetime
import os
import plotly.express as px

import matplotlib.pyplot as plt
import matplotlib as mpl

%matplotlib inline

#remove print limit to better explore dataframe data
pd.set_option('display.max_rows', 300)

In [6]:
iso3 = pd.read_csv("../geodata/ISO3.csv",  index_col = 0)
response = requests.get('https://coronavirus-tracker-api.herokuapp.com/v2/locations?timelines=1')
timeline_raw = response.json()
location_data = timeline_raw['locations']

In [7]:
#Create empty Dataframe
columns = [
        'country',
        'country_code', 
        'country_population',
        'province', 
        'latitude', 
        'longitude',
        'deaths',
        'adjusted_deaths_per_1m',
        'date'
]

top_25 = [
        'Macao SAR',
        'Luxembourg',
        'Singapore',
        'Ireland',
        'Brunei Darussalam',
        'Norway',
        'United Arab Emirates',
        'Kuwait',
        'Switzerland',
        'United States',
        'Hong Kong SAR',
        'San Marino',
        'Netherlands',
        'Iceland',
        'Saudi Arabia',
        'Taiwan Province of China',
        'Sweden',
        'Denmark',
        'Germany',
        'Austria',
        'Australia',
        'Bahrain',
        'Canada',
        'Belgium',
        'United Kingdom'
]

In [9]:
#initialize empty list for data storage
data = []

#Extract COVID mortality data from COVID JSON
for loc in location_data:

#Remove non-countries and countries with missing data
    if loc['country'] in ['MS Zaandam', 'Eritrea', 'Diamond Princess']: continue

    country = loc['country']
    #change US to match imported Coronavirus Data
    if country == 'US': country = 'United States' 
    
    country_code = loc['country_code']
    population = loc['country_population']
    province = loc['province']
    last_updated = loc['last_updated']
    latitude, longitude =  [*loc['coordinates'].values()]

    for record in loc['timelines']['deaths']['timeline'].items():
        date, deaths =  [*record]
        adjusted_deaths_per_1m = int(deaths /  population * 1000000)
        date =  date[:10] + " " + date[11:-1]
        data_row = [country, country_code, population, province, latitude, longitude, deaths, adjusted_deaths_per_1m, date]
        data.append(data_row)

#Convert Data to DataFrame & merge with ISO data
df = pd.DataFrame(columns = columns,
                  data = data).merge(iso3, 
                                     left_on = 'country',
                                     right_on = 'Country')
        

In [15]:
# Group by Country and Date, to remove redundant records (for example, 
# one UK timeline per island / territory)

grouped = df.groupby(['country', 
                     'country_population', 
                      'date',
                     'ISO-3']).agg({'deaths':'sum', 
                                    'adjusted_deaths_per_1m':'sum'}).reset_index()


#Examine temporal trend in death rate
# afghanistan = df[['country', 'deaths', 'date', 'province']][f]
filtered = df[df['country'].isin(top_25)]
# # filtered.index = df['date']
filtered.sort_values('date', inplace = True)
filtered.reset_index(inplace = True)
# filtered['month'] = pd.to_datetime(filtered['date']).dt.to_period('M')
filtered['month'] = filtered['date'].str.slice(5,7)
filtered.columns
dm = filtered[['country', 'adjusted_deaths_per_1m', 'deaths', 'date']].set_index('country')
# dm.plot(kind = 'line', 
#               x = 'date', 
#               y = 'deaths', 
#              figsize = (20,10))



<ipython-input-15-6b512955664f>:15: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-15-6b512955664f>:18: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



country country_code  country_population province latitude  \
73094  United States           US           327167434              40.0   
73095  United States           US           327167434              40.0   
73096  United States           US           327167434              40.0   
73097  United States           US           327167434              40.0   
73098  United States           US           327167434              40.0   
...              ...          ...                 ...      ...      ...   
73411  United States           US           327167434              40.0   
73412  United States           US           327167434              40.0   
73413  United States           US           327167434              40.0   
73414  United States           US           327167434              40.0   
73415  United States           US           327167434              40.0   

      longitude  deaths  adjusted_deaths_per_1m                 date ISO-3  
73094    -100.0       0                       0  2020-01-22 00:00:00   USA  
73095    -100.0       0                       0  2020-01-23 00:00:00   USA  
73096    -100.0       0                       0  2020-01-24 00:00:00   USA  
73097    -100.0       0                       0  2020-01-25 00:00:00   USA  
73098    -100.0       0                       0  2020-01-26 00:00:00   USA  
...         ...     ...                     ...                  ...   ...  
73411    -100.0  278932                     852  2020-12-04 00:00:00   USA  
73412    -100.0  281186                     859  2020-12-05 00:00:00   USA  
73413    -100.0  282299                     862  2020-12-06 00:00:00   USA  
73414    -100.0  283703                     867  2020-12-07 00:00:00   USA  
73415    -100.0  286249                     874  2020-12-08 00:00:00   USA  

[322 rows x 10 columns]

In [16]:
#Plotting using Plotly
def create_line_chart(df, countries:list, metric:str, title:str, ylog = False):
    included = df[df['country'].isin(countries)]
# syntax of all the plotly charts
    fig = px.line(included,
            x = 'date', 
            y = metric, 
            title = title, 
            color = 'country',
            text = metric, 
            template='plotly_dark', 
            log_y = False,
            labels = dict(
                x = 'Date', 
                y = str(metric).title(),
                country = 'Country', 
                deaths = 'Deaths', 
                date = 'Date')
            )
    fig.update_traces(mode='lines')
    
    fig.show()

    
# adjusted = create_line_chart(grouped, top_25, 'deaths', 'Crude Mortality in Top 25 Countries by Per Capita GDP' )
# unadjusted = create_line_chart(grouped, top_25, 'adjusted_deaths_per_1m', 'Population- Adjusted Mortality Rate in Top 25 Countries, by Per Capita GDP' )
# adjusted_ylog = create_line_chart(grouped, top_25, 'deaths', 'Crude Mortality in Top 25 Countries by Per Capita GDP', True)
# unadjusted_ylog = create_line_chart(grouped, top_25, 'adjusted_deaths_per_1m', 'Population- Adjusted Mortality Rate in Top 25 Countries, by Per Capita GDP', True )




In [44]:
notable = ['United States',  
           'Germany', 
           'Switzerland', 
           'Sweden', 
           'Singapore', 
           'Vietnam', 
           'United Arab Emirates', 
           'Italy',
           'United Kingdom']
adjusted = create_line_chart(grouped, 
                             notable, 
                             'adjusted_deaths_per_1m', 
                             'Population-Adjusted Cumulative COVID-19 Mortality Rate')

In [347]:
a  = pd.DataFrame(columns = {'cat', 'dog'})
b = pd.DataFrame([['woof','meow']] )


one = []
two = [4,5,6]
three = [7,8,9]
one.append(two)
one.append(three)
one

[[4, 5, 6], [7, 8, 9]]

In [45]:
px.choropleth(grouped,               
              locations="ISO-3",               
              color='adjusted_deaths_per_1m',
              hover_name="country",  
              animation_frame="date",    
              color_continuous_scale='Amp',  
              width = 1000, 
              range_color = (0,1000),
              title = "Test"
)


3333.3333333333335

In [ ]:
response = requests.get("https://jsonplaceholder.typicode.com/todos")
todos = json.loads(response.text)
type(todos)

In [ ]:
locations_json = covid19.getLocations(timelines=True)
#save data to a file
with open('locations.json', 'w') as fp:
    json.dump(locations_json, fp, indent = 4)

In [ ]:
df = pd.DataFrame(location_json)
df
zzz

In [7]:
a = {1,2}
b,c = [*a]

In [8]:
b

1

In [62]:
a = '2222-11-00xxxx'
a[0:10]


'2222-11-00'

In [31]:
['Macao SAR',
'Luxembourg',
'Singapore',
'Ireland',
'Brunei Darussalam',
'Norway',
'United Arab Emirates',
'Kuwait',
'Switzerland',
'United States',
'Hong Kong SAR',
'San Marino',
'Netherlands',
'Iceland',
'Saudi Arabia',
'Taiwan Province of China',
'Sweden',
'Denmark',
'Germany',
'Austria',
'Australia',
'Bahrain',
'Canada',
'Belgium']

True

In [ ]:
# pd.to_datetime(df_permits['Issued'].str.strip(), yearfirst = True)

In [212]:
#         date = pd.to_datetime(date[0:10], yearfirst = True)
a = 'cat hat djfo a'.title()

In [213]:
a

'Cat Hat Djfo A'